<a href="https://colab.research.google.com/github/lechemrc/DS-Unit-2-Kaggle-Challenge/blob/master/module3/assignment_kaggle_challenge_3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science, Unit 2: Predictive Modeling

# Kaggle Challenge, Module 3


## Assignment
- [ ] [Review requirements for your portfolio project](https://lambdaschool.github.io/ds/unit2), then submit your dataset.
- [ ] Continue to participate in our Kaggle challenge. 
- [ ] Use scikit-learn for hyperparameter optimization with RandomizedSearchCV.
- [ ] Submit your predictions to our Kaggle competition. (Go to our Kaggle InClass competition webpage. Use the blue **Submit Predictions** button to upload your CSV file. Or you can use the Kaggle API to submit your predictions.)
- [ ] Commit your notebook to your fork of the GitHub repo.

## Stretch Goals

### Reading
- Jake VanderPlas, [Python Data Science Handbook, Chapter 5.3](https://jakevdp.github.io/PythonDataScienceHandbook/05.03-hyperparameters-and-model-validation.html), Hyperparameters and Model Validation
- Jake VanderPlas, [Statistics for Hackers](https://speakerdeck.com/jakevdp/statistics-for-hackers?slide=107)
- Ron Zacharski, [A Programmer's Guide to Data Mining, Chapter 5](http://guidetodatamining.com/chapter5/), 10-fold cross validation
- Sebastian Raschka, [A Basic Pipeline and Grid Search Setup](https://github.com/rasbt/python-machine-learning-book/blob/master/code/bonus/svm_iris_pipeline_and_gridsearch.ipynb)
- Peter Worcester, [A Comparison of Grid Search and Randomized Search Using Scikit Learn](https://blog.usejournal.com/a-comparison-of-grid-search-and-randomized-search-using-scikit-learn-29823179bc85)

### Doing
- In additon to `RandomizedSearchCV`, scikit-learn has [`GridSearchCV`](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html). Another library called scikit-optimize has [`BayesSearchCV`](https://scikit-optimize.github.io/notebooks/sklearn-gridsearchcv-replacement.html). Experiment with these alternatives.
- _[Introduction to Machine Learning with Python](http://shop.oreilly.com/product/0636920030515.do)_ discusses options for "Grid-Searching Which Model To Use" in Chapter 6:

> You can even go further in combining GridSearchCV and Pipeline: it is also possible to search over the actual steps being performed in the pipeline (say whether to use StandardScaler or MinMaxScaler). This leads to an even bigger search space and should be considered carefully. Trying all possible solutions is usually not a viable machine learning strategy. However, here is an example comparing a RandomForestClassifier and an SVC ...

The example is shown in [the accompanying notebook](https://github.com/amueller/introduction_to_ml_with_python/blob/master/06-algorithm-chains-and-pipelines.ipynb), code cells 35-37. Could you apply this concept to your own pipelines?


### More Categorical Encodings

**1.** The article **[Categorical Features and Encoding in Decision Trees](https://medium.com/data-design/visiting-categorical-features-and-encoding-in-decision-trees-53400fa65931)** mentions 4 encodings:

- **"Categorical Encoding":** This means using the raw categorical values as-is, not encoded. Scikit-learn doesn't support this, but some tree algorithm implementations do. For example, [Catboost](https://catboost.ai/), or R's [rpart](https://cran.r-project.org/web/packages/rpart/index.html) package.
- **Numeric Encoding:** Synonymous with Label Encoding, or "Ordinal" Encoding with random order. We can use [category_encoders.OrdinalEncoder](https://contrib.scikit-learn.org/categorical-encoding/ordinal.html).
- **One-Hot Encoding:** We can use [category_encoders.OneHotEncoder](http://contrib.scikit-learn.org/categorical-encoding/onehot.html).
- **Binary Encoding:** We can use [category_encoders.BinaryEncoder](http://contrib.scikit-learn.org/categorical-encoding/binary.html).


**2.** The short video 
**[Coursera — How to Win a Data Science Competition: Learn from Top Kagglers — Concept of mean encoding](https://www.coursera.org/lecture/competitive-data-science/concept-of-mean-encoding-b5Gxv)** introduces an interesting idea: use both X _and_ y to encode categoricals.

Category Encoders has multiple implementations of this general concept:

- [CatBoost Encoder](http://contrib.scikit-learn.org/categorical-encoding/catboost.html)
- [James-Stein Encoder](http://contrib.scikit-learn.org/categorical-encoding/jamesstein.html)
- [Leave One Out](http://contrib.scikit-learn.org/categorical-encoding/leaveoneout.html)
- [M-estimate](http://contrib.scikit-learn.org/categorical-encoding/mestimate.html)
- [Target Encoder](http://contrib.scikit-learn.org/categorical-encoding/targetencoder.html)
- [Weight of Evidence](http://contrib.scikit-learn.org/categorical-encoding/woe.html)

Category Encoder's mean encoding implementations work for regression problems or binary classification problems. 

For multi-class classification problems, you will need to temporarily reformulate it as binary classification. For example:

```python
encoder = ce.TargetEncoder(min_samples_leaf=..., smoothing=...) # Both parameters > 1 to avoid overfitting
X_train_encoded = encoder.fit_transform(X_train, y_train=='functional')
X_val_encoded = encoder.transform(X_train, y_val=='functional')
```

**3.** The **[dirty_cat](https://dirty-cat.github.io/stable/)** library has a Target Encoder implementation that works with multi-class classification.

```python
 dirty_cat.TargetEncoder(clf_type='multiclass-clf')
```
It also implements an interesting idea called ["Similarity Encoder" for dirty categories](https://www.slideshare.net/GaelVaroquaux/machine-learning-on-non-curated-data-154905090).

However, it seems like dirty_cat doesn't handle missing values or unknown categories as well as category_encoders does. And you may need to use it with one column at a time, instead of with your whole dataframe.

**4. [Embeddings](https://www.kaggle.com/learn/embeddings)** can work well with sparse / high cardinality categoricals.

_**I hope it’s not too frustrating or confusing that there’s not one “canonical” way to encode categorcals. It’s an active area of research and experimentation! Maybe you can make your own contributions!**_

### BONUS: Stacking!

Here's some code you can use to "stack" multiple submissions, which is another form of ensembling:

```python
import pandas as pd

# Filenames of your submissions you want to ensemble
files = ['submission-01.csv', 'submission-02.csv', 'submission-03.csv']

target = 'status_group'
submissions = (pd.read_csv(file)[[target]] for file in files)
ensemble = pd.concat(submissions, axis='columns')
majority_vote = ensemble.mode(axis='columns')[0]

sample_submission = pd.read_csv('sample_submission.csv')
submission = sample_submission.copy()
submission[target] = majority_vote
submission.to_csv('my-ultimate-ensemble-submission.csv', index=False)
```

### Colab Setup

In [0]:
import os, sys
in_colab = 'google.colab' in sys.modules

# If you're in Colab...
if in_colab:
    # Pull files from Github repo
    os.chdir('/content')
    !git init .
    !git remote add origin https://github.com/LambdaSchool/DS-Unit-2-Kaggle-Challenge.git
    !git pull origin master
    
    # Install required python packages
    !pip install -r requirements.txt
    
    # Change into directory for module
    os.chdir('module3')

Initialized empty Git repository in /content/.git/
remote: Enumerating objects: 85, done.
remote: Total 85 (delta 0), reused 0 (delta 0), pack-reused 85
Unpacking objects: 100% (85/85), done.
From https://github.com/LambdaSchool/DS-Unit-2-Kaggle-Challenge
 * branch            master     -> FETCH_HEAD
 * [new branch]      master     -> origin/master
     |████████████████████████████████| 92kB 3.6MB/s 
     |████████████████████████████████| 112kB 9.2MB/s 
     |████████████████████████████████| 133kB 53.3MB/s 
     |████████████████████████████████| 57.7MB 1.3MB/s 
     |████████████████████████████████| 245kB 35.3MB/s 
     |████████████████████████████████| 614kB 44.3MB/s 
     |████████████████████████████████| 225kB 48.3MB/s 
     |████████████████████████████████| 307kB 56.2MB/s 
     |████████████████████████████████| 51kB 24.5MB/s 
     |████████████████████████████████| 194kB 56.4MB/s 
     |████████████████████████████████| 51kB 24.2MB/s 
     |████████████████████████████████

### Important imports and libraries

In [0]:
# libraries and math functions
import pandas as pd
import numpy as np
import pandas_profiling
from scipy.stats import randint, uniform

# imports for pipeline and regression
import category_encoders as ce
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.pipeline import make_pipeline
from sklearn.impute import SimpleImputer
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.linear_model import LogisticRegression, Ridge
from sklearn.preprocessing import StandardScaler
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import f_regression, SelectKBest
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.model_selection import validation_curve
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.cluster import KMeans

# plotting
%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px

### Importing, cleaning, and splitting data + mild feature engineering

In [0]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

# Merge train_features.csv & train_labels.csv
train = pd.merge(pd.read_csv('../data/tanzania/train_features.csv'), 
                 pd.read_csv('../data/tanzania/train_labels.csv'))

# Read test_features.csv & sample_submission.csv
test = pd.read_csv('../data/tanzania/test_features.csv')
sample_submission = pd.read_csv('../data/tanzania/sample_submission.csv')

In [0]:
# Test Train Split 
train, val = train_test_split(train, train_size=0.80, test_size=0.20, 
                              stratify=train['status_group'], random_state=42)


def wrangle(X):
    """Wrangle train, validate, and test sets in the same way"""
    
    # Prevent SettingWithCopyWarning
    X = X.copy()
    
    # About 3% of the time, latitude has small values near zero,
    # outside Tanzania, so we'll treat these values like zero.
    X['latitude'] = X['latitude'].replace(-2e-08, 0)
    
    # When columns have zeros and shouldn't, they are like null values.
    # So we will replace the zeros with nulls, and impute missing values later.
    # Also create a "missing indicator" column, because the fact that
    # values are missing may be a predictive signal.
    cols_with_zeros = ['longitude', 'latitude', 'construction_year', 
                       'gps_height', 'population']
    for col in cols_with_zeros:
        X[col] = X[col].replace(0, np.nan)
        X[col+'_MISSING'] = X[col].isnull()
            
    # Drop duplicate columns
    duplicates = ['quantity_group', 'payment_type']
    X = X.drop(columns=duplicates)
    
    # Drop recorded_by (never varies) and id (always varies, random)
    unusable_variance = ['recorded_by', 'id']
    X = X.drop(columns=unusable_variance)
    
    # Convert date_recorded to datetime
    X['date_recorded'] = pd.to_datetime(X['date_recorded'], infer_datetime_format=True)
    
    # Extract components from date_recorded, then drop the original column
    X['year_recorded'] = X['date_recorded'].dt.year
    X['month_recorded'] = X['date_recorded'].dt.month
    X['day_recorded'] = X['date_recorded'].dt.day
    X = X.drop(columns='date_recorded')
    
    # Engineer feature: how many years from construction_year to date_recorded
    X['years'] = X['year_recorded'] - X['construction_year']
    X['years_MISSING'] = X['years'].isnull()
    
    # return the wrangled dataframe
    return X

train = wrangle(train)
val = wrangle(val)
test = wrangle(test)

In [0]:
# The status_group column is the target
target = 'status_group'

# put together our numeric and categorical features
train_features = train.drop(columns=[target])
numeric_features = train_features.select_dtypes(include='number').columns.tolist()
cardinality = train_features.select_dtypes(exclude='number').nunique()
categorical_features = cardinality[cardinality <= 50].index.tolist()

features = numeric_features + categorical_features

In [0]:
# Arrange data into X features matrix and y target vector 
X_train = train[features]
y_train = train[target]
X_val = val[features]
y_val = val[target]
X_test = test[features]

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape

((47520, 38), (47520,), (11880, 38), (11880,), (14358, 38))

### Profile Report

In [0]:
train.profile_report()

### Baseline Regression

Training Accuracy: 0.5430765993265994 <br>
Validation Score: 0.5430976430976431

In [0]:
# location for benchmark
train_location = X_train[['longitude', 'latitude']].copy()
val_location = X_val[['longitude', 'latitude']].copy()

# creating a pipeline that has:
# SimpleImputer, and LogisticRegression
# To establish a baseline
log_reg = make_pipeline(
    SimpleImputer(),
    LogisticRegression(multi_class='auto', solver='lbfgs', n_jobs=-1)
)

log_reg.fit(train_location, y_train)
print('Training Accuracy:', log_reg.score(train_location, y_train))
print('Validation Score:', log_reg.score(val_location, y_val))

Training Accuracy: 0.5430765993265994
Validation Score: 0.5430976430976431


### Futher Feature Engineering

#### Status Group plot

In [0]:
px.scatter(train, x='longitude', y='latitude', color='status_group')

#### Checking for nulls

In [0]:
train.isna().sum()

amount_tsh                       0
funder                        2904
gps_height                   16305
installer                     2917
longitude                     1442
latitude                      1442
wpt_name                         0
num_private                      0
basin                            0
subvillage                     286
region                           0
region_code                      0
district_code                    0
lga                              0
ward                             0
population                   17066
public_meeting                2644
scheme_management             3128
scheme_name                  22532
permit                        2443
construction_year            16517
extraction_type                  0
extraction_type_group            0
extraction_type_class            0
management                       0
management_group                 0
payment                          0
water_quality                    0
quality_group       

Longitude and Latitude both have 1442 missing values. With a dataset of 47520 values, that is 3% of the data. I will fill them based on the mean of the basin's corresponding longitude and latitude

#### Engineering the longitude and latitude

In [0]:
px.scatter(train, x='longitude', y='latitude', color='basin')

In [0]:
train.head(1)

amount_tsh funder  gps_height  ... day_recorded  years  years_MISSING
43360         0.0    NaN         NaN  ...           27    NaN           True

[1 rows x 46 columns]

In [0]:
train.groupby('basin')[['longitude', 'latitude']].mean()

longitude   latitude
basin                                        
Internal                 34.947979  -4.168195
Lake Nyasa               34.247372  -9.703113
Lake Rukwa               32.388582  -8.288800
Lake Tanganyika          31.209497  -4.601597
Lake Victoria            32.770892  -2.242988
Pangani                  37.619867  -3.922940
Rufiji                   35.849989  -8.396395
Ruvuma / Southern Coast  38.325058 -10.486821
Wami / Ruvu              37.888604  -6.584763

In [0]:
basin_mean = train.groupby('basin')[['longitude', 'latitude']].mean().reset_index()
basin_mean

basin  longitude   latitude
0                 Internal  34.947979  -4.168195
1               Lake Nyasa  34.247372  -9.703113
2               Lake Rukwa  32.388582  -8.288800
3          Lake Tanganyika  31.209497  -4.601597
4            Lake Victoria  32.770892  -2.242988
5                  Pangani  37.619867  -3.922940
6                   Rufiji  35.849989  -8.396395
7  Ruvuma / Southern Coast  38.325058 -10.486821
8              Wami / Ruvu  37.888604  -6.584763

In [0]:
# PSEUDOCODE
# for each value train['longitude']:
#   if it is a NaN:
#     change value to mean longitude of corresponding basin

In [0]:
# # changing longitude NaNs
# for value in train['longitude']:
#   if value == None:
#     value = 

In [0]:
# Changing NaNs in long and lat to 0 to then change to mean

train['longitude'] = train['longitude'].fillna(value=0)
train['latitude'] = train['latitude'].fillna(value=0)

test['longitude'] = test['longitude'].fillna(value=0)
test['latitude'] = test['latitude'].fillna(value=0)

val['longitude'] = val['longitude'].fillna(value=0)
val['latitude'] = val['latitude'].fillna(value=0)

In [0]:
# Code from Michael

train.loc[train['longitude'] == 0, 'longitude'] = train.groupby(
                                 'basin')['longitude'].transform('mean')

test.loc[test['longitude'] == 0, 'longitude'] = test.groupby(
                                 'basin')['longitude'].transform('mean')

val.loc[test['longitude'] == 0, 'longitude'] = val.groupby(
                                 'basin')['longitude'].transform('mean')

IndexingError: ignored

#### Function for replacing specific columns' NaNs with the mean or mode of a specific groupby

In [0]:
def replacing_nulls_with_mmm(train, test, feature, ref_feature, method):
  ''' replacing a column's null values in train and test data with a specified
  feature based on the mean, median, or mode of a specific groupby column'''

  train[feature] = train[feature].fillna(value=0)

  train.loc[train[feature] == 0, feature] = train.groupby(
                                 ref_feature)[feature].transform(method)
  test.loc[test[feature] == 0, feature] = test.groupby(
                                 ref_feature)[feature].transform(method)

#### KMeans clustering

In [0]:
test.isna().sum()

In [0]:
# Cluster the locations
from sklearn.cluster import KMeans
kmeans = KMeans(n_clusters = 8, n_jobs = -1) 

train['cluster'] = kmeans.fit_predict(train[['longitude', 'latitude']])
test['cluster'] = kmeans.fit_predict(test[['longitude', 'latitude']])
val['cluster'] = kmeans.fit_predict(val[['longitude', 'latitude']])
px.scatter(train, x='longitude', y='latitude', color='cluster')

In [0]:
# Re-running this to make sure the datasets are still accurate

# Arrange data into X features matrix and y target vector 
X_train = train[features]
y_train = train[target]
X_val = val[features]
y_val = val[target]
X_test = test[features]

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape

In [0]:
# Random Forest with One Hot Encoding
random_forest = make_pipeline(
    ce.OneHotEncoder(use_cat_names=True),
    SimpleImputer(),
    RandomForestClassifier(n_estimators=6, random_state=42, n_jobs=-1)
)

random_forest.fit(X_train, y_train)
print('Validation Accuracy', random_forest.score(X_val, y_val))

Clustering helped improve the accuracy to 79.27% which is great progress! Almost past that 80% mark

#### More Feature Engineering

In [0]:
train.isna().sum()

In [0]:
train.head()

In [0]:
train.columns

In [0]:
# replacing_nulls_with_mmm(train, test, 'installer', 'basin', 'mean')

In [0]:
# The status_group column is the target
target = 'status_group'

# put together our numeric and categorical features
train_features = train.drop(columns=[target, 'num_private', 'funder', 
                                      'longitude_MISSING', 'latitude_MISSING', 
                                      'construction_year_MISSING', 
                                      'population_MISSING', 'gps_height_MISSING', 
                                      'years_MISSING'])
numeric_features = train_features.select_dtypes(include='number').columns.tolist()
cardinality = train_features.select_dtypes(exclude='number').nunique()
categorical_features = cardinality[cardinality <= 50].index.tolist()

features = numeric_features + categorical_features

In [0]:
# Re-running this to make sure the datasets are still accurate

# Arrange data into X features matrix and y target vector 
X_train = train[features]
y_train = train[target]
X_val = val[features]
y_val = val[target]
X_test = test[features]

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape

#### Using KBest to select features -- Currently not working


In [0]:
kbest = make_pipeline(
    ce.OneHotEncoder(use_cat_names=True),
    SimpleImputer(),
    StandardScaler(),
    SelectKBest(score_func = f_regression, k = 15),
    RandomForestClassifier(n_estimators=6, random_state=42, n_jobs=-1)
)

kbest.fit(X_train, y_train)
print('Validation Accuracy', kbest.score(X_val, y_val))

In [0]:
# Which features were selected?

all_names = X_train.columns
selected_mask = selector.get_support()
selected_names = all_names[selected_mask]
unselected_names = all_names[~selected_mask]

print('Features selected:')
for name in selected_names:
  print(name)

### Running RandomSearchCV on regression analysis


#### Random Forest with Simple Imputer

Clustering and dropping some columns may help improve score

In [0]:
rfc = make_pipeline(
    ce.OneHotEncoder(use_cat_names=True),
    SimpleImputer(),
    StandardScaler(),
    RandomForestClassifier(n_estimators=15, n_jobs=-1, random_state=42)
)

rfc.fit(X_train, y_train)
print('Validation Score:', rfc.score(X_val, y_val))

#### Running Randomized Search CV on classifier

In [0]:
# The status_group column is the target
target = 'status_group'

# put together our numeric and categorical features
train_features = train.drop(columns=[target, 'num_private', 'funder', 
                                      'longitude_MISSING', 'latitude_MISSING', 
                                      'construction_year_MISSING', 
                                      'population_MISSING', 'gps_height_MISSING', 
                                      'years_MISSING'])
numeric_features = train_features.select_dtypes(include='number').columns.tolist()
cardinality = train_features.select_dtypes(exclude='number').nunique()
categorical_features = cardinality[cardinality <= 50].index.tolist()

features = numeric_features + categorical_features

In [0]:
# Re-running this to make sure the datasets are still accurate

# Arrange data into X features matrix and y target vector 
X_train = train[features]
y_train = train[target]
X_val = val[features]
y_val = val[target]
X_test = test[features]

X_train.shape, y_train.shape, X_val.shape, y_val.shape, X_test.shape

In [0]:
rfc2 = make_pipeline(
    ce.OneHotEncoder(use_cat_names=True),
    SimpleImputer(),
    RandomForestClassifier(n_estimators=200, n_jobs=-1, 
                           random_state=42)
)

rfc2.fit(X_train, y_train)
print('Validation Score:', rfc2.score(X_val, y_val))

y_pred = rfc2.predict(X_test)

In [0]:
rfc2 = make_pipeline(
    ce.OneHotEncoder(use_cat_names=True),
    SimpleImputer(),
    RandomForestClassifier()
)

param_distributions = {
    'simpleimputer__strategy': ['mean', 'median'], 
    'randomforestclassifier__n_estimators': randint(50, 500), 
    'randomforestclassifier__max_depth': [5, 10, 15, 20, None]
}

search = RandomizedSearchCV(
    rfc2, 
    param_distributions=param_distributions, 
    n_iter=10, 
    cv=3, 
    scoring='neg_mean_absolute_error', 
    verbose=10, 
    return_train_score=True, 
    n_jobs=-1
)

search.fit(X_train, y_train);

## Submitting to Kaggle

In [0]:
rfc2 = make_pipeline(
    ce.OneHotEncoder(use_cat_names=True),
    SimpleImputer(),
    RandomForestClassifier(n_estimators=200, n_jobs=-1, random_state=42)
)

rfc2.fit(X_train, y_train)
print('Validation Score:', rfc2.score(X_val, y_val))

y_pred = rfc2.predict(X_test)

In [0]:
submission = sample_submission.copy()
submission['status_group'] = y_pred
submission.to_csv('rob_lecheminant_submission-03.csv', index=False)

In [0]:
!head rob_lecheminant_submission-03.csv

In [0]:
if in_colab:
  from google.colab import files
  files.download('rob_lecheminant_submission-03.csv')